# Άσκηση 12 - Αυτοκωδικοποιητές

## 1. Εισαγωγή

### 1.α. Βιβλιοθήκες

In [ ]:
from tensorflow.keras import regularizers
from tensorflow.keras.datasets import mnist
from tensorflow.keras.layers import Input, Dense
from tensorflow.keras.models import Sequential
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics.pairwise import cosine_similarity

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

# Θέτουμε σπορά (seed) στη γεννήτρια ψευδο-τυχαίων αριθμών για να λάβουμε
# ίδια αποτελέσματα

np.random.seed(2022)

### 1.β. Βοηθητικές συναρτήσεις

In [ ]:
def compare_digits(test, decoded, n=10):
  plt.figure(figsize=(20, 4))
  for i in range(n):
      # display original
      ax = plt.subplot(2, n, i + 1)
      plt.imshow(test[i].reshape(28, 28))
      plt.gray()
      ax.get_xaxis().set_visible(False)
      ax.get_yaxis().set_visible(False)

      # display reconstruction
      ax = plt.subplot(2, n, i + 1 + n)
      plt.imshow(decoded[i].reshape(28, 28))
      plt.gray()
      ax.get_xaxis().set_visible(False)
      ax.get_yaxis().set_visible(False)
  plt.show()
  
  
def display_digits(data, n=10):
  plt.figure(figsize=(20, 2))
  for i in range(n):
    ax = plt.subplot(1, n, i + 1)
    plt.imshow(data[i].reshape(28, 28))
    plt.gray()
    ax.get_xaxis().set_visible(False)
    ax.get_yaxis().set_visible(False)
  plt.show()

### 1.γ. Δεδομένα

In [ ]:
(x_train, _), (x_test, _) = mnist.load_data()

x_train = x_train.reshape((len(x_train), np.prod(x_train.shape[1:])))
x_test = x_test.reshape((len(x_test), np.prod(x_test.shape[1:])))

scaler = MinMaxScaler()
x_train = scaler.fit_transform(x_train)
x_test = scaler.fit_transform(x_test)

print(x_train.shape)
print(x_test.shape)

## 2. Υποπλήρης Αυτοκωδικοποιητής

Βάση εργασίας αποτελεί ο υποπλήρης αυτοκωδικοποιητής που δείξαμε στο εργαστήριο

### 2.1.  Αντιστρέψετε τις συναρτήσεις (απο)κωδικοποίησης. Τι παρατηρείτε;


In [ ]:
dim_x = 28*28
dim_h = 32

autoencoder = Sequential([
    Dense(dim_h, activation='sigmoid', input_shape=(dim_x,)),
    Dense(dim_x, activation='relu')
])


autoencoder.compile(optimizer='adam', loss='binary_crossentropy')

autoencoder.fit(x_train, x_train,
                epochs=20,
                batch_size=64,
                shuffle=True,
                validation_data=(x_test, x_test))

Παρατηρούμε ότι αντιστρέφοντας τις συναρτήσεις ενεργοποίησης (χρησιμοποιώντας σιγμοειδή στον κωδικοποιητή αντί του αποκωδικοποιητή και relu στον αποκωδικοποιητή αντί του κωδικοποιητή) τα σφάλματα εκπαίδευσης και επαλήθευσης είναι αρκετά πιο μεγάλα σε σύγκριση με τα αντίστοιχα που είχαμε επιτύχει στο εργαστήριο (γύρω στο $0.40$ αντί του $0.09$).

Ας εξετάσουμε τι επίδραση έχει στην ποιότητα των αναδημιουργημένων εικόνων.

In [ ]:
encoder = Sequential([
    autoencoder.layers[-2]
])

decoder = Sequential([
    autoencoder.layers[-1]
])

h = encoder.predict(x_test)
x_test_out = decoder.predict(h)

compare_digits(x_test, x_test_out)

Παρατηρούμε ότι σε σύγκριση με τις αντίστοιχες εικόνες του υποπλήρη αυτοκωδικοποιητή του εργαστηρίου, εδώ η ποιότητα έχει σαφώς χειροτερεύσει (εισαγωγή artifacts κλπ). Συνεπώς οι παράμετροι και των δύο δικτύων παίζουν πολύ μεγάλο ρόλο στη συνολική απόδοση του αυτοκωδικοποιητή.

### 2.2. Χρησιμοποιείστε την ίδια συνάρτηση κωδικοποίησης και αποκωδικοποίησης (λχ τη relu). Τι παρατηρείτε;

In [ ]:
autoencoder = Sequential([
    Dense(dim_h, activation='relu', input_shape=(dim_x,)),
    Dense(dim_x, activation='relu')
])


autoencoder.compile(optimizer='adam', loss='binary_crossentropy')

autoencoder.fit(x_train, x_train,
                epochs=20,
                batch_size=64,
                shuffle=True,
                validation_data=(x_test, x_test))

Παρατηρούμε πως και σε αυτή την περίπτωση το σφάλμα εκπαίδευσης είναι μεγαλύτερο από τον υποπλήρη αυτοκωδικοποιητή που δείξαμε στο εργαστήριο (περίπου το διπλάσιο). Έτσι όπως είναι σχεδιασμένο το δίκτυο, δεν υπάρχει κάποιος μηχανισμός που να το αποτρέπει από το να αντιγράφει την είσοδό του στην έξοδό του, με αποτέλεσμα να μην αποτυπώνει τα χαρακτηριστικά της εισόδου του στον λανθάνοντα χώρο, σε ικανοποιητικό βαθμό.

Όπως και στην προηγούμενη περίπτωση, ας εξετάσουμε την επίδραση του δικτύου στις αναδημιουργούμενες εικόνες.

In [ ]:
encoder = Sequential([
    autoencoder.layers[-2]
])

decoder = Sequential([
    autoencoder.layers[-1]
])

h = encoder.predict(x_test)
x_test_out = decoder.predict(h)

compare_digits(x_test, x_test_out)

Και σε αυτή την περίπτωση, η ποιότητα έχει σαφώς χειροτερεύσει (θόλωμα, artifacts κλπ). Συνεπώς, είναι σημαντικό να σχεδιάζουμε δίκτυα αυτοκωδικοποίησης που μπορούν να μαθαίνουν τα χαρακτηριστικά της εισόδου τους.

## 3. Αραιός Αυτοκωδικοποιητής

Βάση εργασίας αποτελεί ο αραιός αυτοκωδικοποιητής που δείξαμε στο εργαστήριο

### 3.1. Δοκιμάστε να αυξήσετε το βάρος της ποινής αραιότητας. Τι παρατηρείτε;

Ας αυξήσουμε το βάρος της ποινής αραιότητας κατά 100, δηλαδή επιλέγοντας $\lambda=0.01$

In [ ]:
sparse_autoencoder = Sequential([
    Dense(dim_h, activation='relu', 
          activity_regularizer=regularizers.l1(0.01), 
          input_shape=(dim_x,)),
    Dense(dim_x, activation='sigmoid')
])


sparse_autoencoder.compile(optimizer='adam', loss='binary_crossentropy')

sparse_autoencoder.fit(x_train, x_train,
                epochs=30,
                batch_size=64,
                shuffle=True,
                validation_data=(x_test, x_test))

Παρατηρούμε πως τα σφάλματα εκπαίδευσης και ελέγχου, ενώ αρχικά μειώνονται, πολύ γρήγορα σταθεροποιούνται σε μια σχετικά μεγάλη τιμή (τουλάχιστον διπλάσια από την αντίστοιχη που είχαμε πετύχει στο εργαστήριο), δείγμα του ότι η εκπαίδευση "κολλάει" σε κάποια τοπικά βέλτιστη λύση.

Στη συνέχεια θα εξετάσουμε την επίδραση του δικτύου στις αναδημιουργούμενες εικόνες.

In [ ]:
sparse_encoder = Sequential([
    sparse_autoencoder.layers[-2]
])

sparse_decoder = Sequential([
    sparse_autoencoder.layers[-1]
])

h_sparse = sparse_encoder.predict(x_test)
x_test_out_sparse = sparse_decoder.predict(h_sparse)

compare_digits(x_test, x_test_out_sparse)

Παρατηρούμε ότι η ποιότητα των εικόνων είναι πάρα πολύ κακή (μια θολή μουντζούρα, ίδια για όλα τα ψηφία). Συνεπώς, αν δεν επιλεγεί ορθά το εύρος της ποινής αραιότητας, βλέπουμε πως όχι μόνο δεν βελτιώνεται η απόδοση του δικτύου, αλλά αντίθετα χειροτερεύει.

## 4. Αυτοκωδικοποιητής απαλοιφής θορύβου

Βάση εργασίας αποτελεί ο αραιός αυτοκωδικοποιητής που δείξαμε στο εργαστήριο.

### 4.1. Δοκιμάστε να μεταβάλλετε (αυξήσετε/μειώσετε) το συντελεστή θορύβου. Τι παρατηρείτε;

Ας διπλασιάσουμε τον συντελεστή θορύβου στο $0.6$

In [ ]:
noise_factor = 0.6
x_train_noisy = x_train + noise_factor * np.random.normal(loc=0.0, scale=1.0, 
                                                          size=x_train.shape) 
x_test_noisy = x_test + noise_factor * np.random.normal(loc=0.0, scale=1.0, 
                                                        size=x_test.shape) 

x_train_noisy = np.clip(x_train_noisy, 0., 1.)
x_test_noisy = np.clip(x_test_noisy, 0., 1.)

noisy_autoencoder = Sequential([
    Dense(dim_h, activation='relu', input_shape=(dim_x,)),
    Dense(dim_x, activation='sigmoid')
])


noisy_autoencoder.compile(optimizer='adam', loss='binary_crossentropy')

noisy_autoencoder.fit(x_train_noisy, x_train,
                epochs=30,
                batch_size=64,
                shuffle=True,
                validation_data=(x_test, x_test))

Παρατηρούμε ότι τα σφάλματα εκπαίδευσης και επαλήθευσης είναι ελαφρώς χειρότερα σε σύγκριση με τις τιμές που παρατηρήθηκαν στο εργαστήριο, παρά τον διπλασιασμό του συντελεστή θορύβου.

Για να δούμε και την επίδρασή του στις παραγόμενες εικόνες.

In [ ]:
noisy_encoder = Sequential([
    noisy_autoencoder.layers[-2]
])

noisy_decoder = Sequential([
    noisy_autoencoder.layers[-1]
])

h_noisy = noisy_encoder.predict(x_test_noisy)
x_test_out_noisy = noisy_decoder.predict(h_noisy)
compare_digits(x_test_noisy, x_test_out_noisy)

Παρότι ο θόρυβος που προστέθηκε ήταν πολύς σε ποσότητα, κάνοντας τα ψηφία σχεδόν μη-αναγνωρίσιμα στο ανθρώπινο μάτι, εντούτοις ο αποκωδικοποιητής απαλοιφής θορύβου κατόρθωσε να τα ανακτήσει σε πολύ ικανοποιητικό βαθμό (είναι μοναχά λίγο πιο θολά από τα αντίστοιχα του αυτοκωδικοποιητή απαλοιφής θορύβου που δείξαμε στο εργαστήριο).

## 5. Βαθύς αυτοκωδικοποιητής

Βάση εργασίας αποτελεί ο βαθύς αυτοκωδικοποιητής που δείξαμε στο εργαστήριο.

### 5.1. Δοκιμάστε να χρησιμοποιήσετε διαφορετικές συναρτήσεις στο επίπεδο αποκωδικοποίησης. Τι παρατηρείτε;

Θα αντικαταστήσουμε τις ημιγραμμικές συναρτήσεις ενεργοποίησης του επιπέδου αποκωδικοποίησης με σιγμοειδείς. 

In [ ]:
layer1_dim = 128
layer2_dim = 64

deep_autoencoder = Sequential([
    Dense(layer1_dim, activation='relu', input_shape=(dim_x,)),
    Dense(layer2_dim, activation='relu'),
    Dense(dim_h, activation='relu'),
    
    Dense(layer2_dim, activation='sigmoid'),
    Dense(layer1_dim, activation='sigmoid'),
    Dense(dim_x, activation='sigmoid')
])


deep_autoencoder.compile(optimizer='adam', loss='binary_crossentropy')

deep_autoencoder.fit(x_train, x_train,
                epochs=30,
                batch_size=64,
                shuffle=True,
                validation_data=(x_test, x_test))

Τα σφάλματα εκπαίδευσης και ελέγχου είναι ελαφρώς χειρότερα σε αυτή την περίπτωση. Ας δούμε και τις παραγόμενες εικόνες

In [ ]:
deep_encoder = Sequential([
    deep_autoencoder.layers[0],
    deep_autoencoder.layers[1],
    deep_autoencoder.layers[2]
])

deep_decoder = Sequential([
    deep_autoencoder.layers[-3],
    deep_autoencoder.layers[-2],
    deep_autoencoder.layers[-1]
])

h_deep = deep_encoder.predict(x_test)
x_test_out_deep = deep_decoder.predict(h_deep)
compare_digits(x_test, x_test_out_deep)

Οι διαφορές είναι πολύ μικρές σε σύγκριση με το αντίστοιχο δίκτυο που δείξαμε στο εργαστήριο. Ωστόσο παρατηρούμε πως ορισμένα ψηφία είναι λίγο περισσότερο θολά.